![](https://github.com/bigdata-icict/ETL-Dataiku-DSS/raw/master/tutoriais/pcdas_1.5.png)

# Notebook para criação de tabela de indicadores da PNS -  módulo P 2013 Consumo de Álcool

## Bibliotecas Utilizadas

In [23]:
#Lendo pacotes necessários
library(survey)
library(ggplot2)
library(dplyr)
library(foreign)
library(forcats)
library(tidyverse)

## Carregando microdados da PNS

In [1]:
#Carregando banco de dados para R versão 3.5.0 ou superior
load("<coloque aqui o caminho para o arquivo dos microdados formato RDATA>")

## Definição do peso e filtragem de respondentes do questionario

In [3]:
#Selecionando registros válidos para o módulo P e calculando peso amostral - summary de verificação
pns2013.1<-pns2013 %>% filter(M001==1)
pns2013.1<-pns2013.1 %>% mutate(peso_morador_selec=((V00291*(60202/145572211))))
pns2013.1<-pns2013.1 %>% filter(!is.na(peso_morador_selec))
summary(pns2013.1$peso_morador_selec)

     Min.   1st Qu.    Median      Mean   3rd Qu.      Max. 
 0.004156  0.243959  0.521557  1.000000  1.147413 31.179597 

## Criação de variáveis dos indicadores

In [4]:
#Desfechos - Indicadores

#P010P - Consumo de bebida alcoólica uma vez ou mais por semana
pns2013.1$P028[which(is.na(pns2013.1$P028))] <- 0
pns2013.1 <- pns2013.1 %>% filter(P028!=9) %>% mutate(P010P = ifelse(P028>=1, 1,2))
pns2013.1$P010P<-factor(pns2013.1$P010P, levels=c(1,2), labels=c("Sim","Nao"))
summary(pns2013.1$P010P)

#P011P - Consumo regular de bebida alcoólica
pns2013.1$P028[which(is.na(pns2013.1$P028))] <- 0
pns2013.1 <- pns2013.1 %>% filter(P028!=9) %>% mutate(P011P = ifelse(P028>=5, 1,2))
pns2013.1$P011P<-factor(pns2013.1$P011P, levels=c(1,2), labels=c("Sim","Nao"))
summary(pns2013.1$P011P)

#P012P - Consumo abusivo de álcool nos últimos 30 dias
pns2013.1$P032[which(is.na(pns2013.1$P032))] <- 0
pns2013.1 <- pns2013.1 %>% filter(P032!=9) %>% mutate(P012P = ifelse(P032==1, 1,2))
pns2013.1$P012P<-factor(pns2013.1$P012P, levels=c(1,2), labels=c("Sim","Nao"))
summary(pns2013.1$P012P)

#P013P - Dirigir automóvel ou motocicleta logo depois de beber nos últimos 12 meses
pns2013.1$P030[which(is.na(pns2013.1$P030))] <- 0
pns2013.1 <- pns2013.1 %>% filter(P030!=9|P030>0) %>% mutate(P013P = ifelse(P030==1, 1,2))
pns2013.1$P013P<-factor(pns2013.1$P013P, levels=c(1,2), labels=c("Sim","Nao"))
summary(pns2013.1$P013P)


Sim   Nao 
13226 46976

Sim   Nao 
 1346 58856

Sim   Nao 
 8104 52098

Sim   Nao 
 2363 57839

## Definições de abrangências

### Situação urbana ou rural

In [5]:
#Situação Urbano ou Rural
pns2013.1 <- pns2013.1 %>% rename(Sit_Urbano_Rural=V0026)
pns2013.1$Sit_Urbano_Rural<-factor(pns2013.1$Sit_Urbano_Rural, levels=c(1,2), labels=c("Urbano", "Rural"))
summary(pns2013.1$Sit_Urbano_Rural)

Urbano  Rural 
 49245  10957

### Sexo

In [6]:
#Sexo
pns2013.1 <- pns2013.1 %>% rename(Sexo=C006)
pns2013.1$Sexo<-factor(pns2013.1$Sexo, levels=c(1,2), labels=c("Masculino", "Feminino"))
summary(pns2013.1$Sexo)

Masculino  Feminino 
    25920     34282

### UF

In [7]:
#Estados - UFs
pns2013.1 <- pns2013.1 %>% rename(Unidades_da_Federacao=V0001)
pns2013.1$Unidades_da_Federacao<-factor(pns2013.1$Unidades_da_Federacao, levels=c(11,12,13,14,15,16,17,21,22,23,24,25,26,27,28,29,31,32,33,35,41,42,43,50,51,52,53),
                                       label=c("Rondonia","Acre","Amazonas","Roraima","Para","Amapa","Tocantins","Maranhao","Piaui","Ceara",
                                        "Rio Grande do Norte","Paraiba","Pernambuco","Alagoas","Sergipe","Bahia",
                                        "Minas Gerais","Espirito Santo","Rio de Janeiro","Sao Paulo",
                                        "Parana","Santa Catarina","Rio Grande do Sul", 
                                        "Mato Grosso do Sul","Mato Grosso","Goias","Distrito Federal"))
summary(pns2013.1$Unidades_da_Federacao)

Rondonia                Acre            Amazonas             Roraima 
               1694                1814                2586                1591 
               Para               Amapa           Tocantins            Maranhao 
               2004                1332                1515                1774 
              Piaui               Ceara Rio Grande do Norte             Paraiba 
               1804                2560                1691                1943 
         Pernambuco             Alagoas             Sergipe               Bahia 
               2591                1748                1553                2641 
       Minas Gerais      Espirito Santo      Rio de Janeiro           Sao Paulo 
               3779                1724                3486                5305 
             Parana      Santa Catarina   Rio Grande do Sul  Mato Grosso do Sul 
               3012                1623                2913                1809 
        Mato Grosso               Goias    Distrito Federal 
               1476                2423                1811

### Grandes Regiões

In [8]:
#Grandes Regiões
pns2013.1 <- pns2013.1 %>% 
  mutate(GrandesRegioes = fct_collapse(Unidades_da_Federacao, 
                                          `1 Norte` = c("Rondonia","Acre","Amazonas","Roraima","Para", "Amapa","Tocantins"),
                                          `2 Nordeste` = c("Maranhao", "Piaui", "Ceara", "Rio Grande do Norte", "Paraiba","Pernambuco", "Alagoas","Sergipe","Bahia"),
                                          `3 Sudeste` = c("Minas Gerais", "Espirito Santo","Rio de Janeiro", "Sao Paulo"), 
                                          `4 Sul` = c("Parana", "Santa Catarina", "Rio Grande do Sul"),
                                          `5 Centro-Oeste`= c("Mato Grosso do Sul","Mato Grosso", "Goias", "Distrito Federal")))
summary(pns2013.1$GrandesRegioes)

1 Norte     2 Nordeste      3 Sudeste          4 Sul 5 Centro-Oeste 
         12536          18305          14294           7548           7519

### Capital

In [9]:
#Capital
pns2013.1<- pns2013.1 %>% mutate(Capital= fct_collapse(Unidades_da_Federacao,
                                        `Porto Velho`= "Rondonia", 
                                        `Boa Vista`= "Roraima",              
                                        `Rio Branco `= "Acre", 
                                        `Manaus` = "Amazonas",
                                        `Boa Vista`= "Roraima",
                                        `Belem` = "Para" ,
                                        `Macapa`= "Amapa",
                                        `Palmas` = "Tocantins",
                                        `Sao Luis` = "Maranhao",
                                        `Teresina`= "Piaui" ,
                                        `Fortaleza`= "Ceara",
                                        `Natal`= "Rio Grande do Norte",
                                        `Joao Pessoa`= "Paraiba",
                                        `Recife`= "Pernambuco",
                                        `Maceio`= "Alagoas",
                                        `Aracaju`= "Sergipe",
                                        `Salvador`= "Bahia",
                                        `Belo Horizonte`= "Minas Gerais",
                                        `Vitoria`= "Espirito Santo",
                                        `Rio de Janeiro`= "Rio de Janeiro",
                                        `Sao Paulo`= "Sao Paulo",
                                        `Curitiba`= "Parana",
                                        `Florianopolis`= "Santa Catarina",
                                        `Porto Alegre`= "Rio Grande do Sul",
                                        `Campo Grande`=  "Mato Grosso do Sul",
                                        `Cuiaba`= "Mato Grosso",
                                        `Goiania` = "Goias",
                                        `Brasilia`= "Distrito Federal"))
summary(pns2013.1$Capital)

Porto Velho    Rio Branco          Manaus      Boa Vista          Belem 
          1694           1814           2586           1591           2004 
        Macapa         Palmas       Sao Luis       Teresina      Fortaleza 
          1332           1515           1774           1804           2560 
         Natal    Joao Pessoa         Recife         Maceio        Aracaju 
          1691           1943           2591           1748           1553 
      Salvador Belo Horizonte        Vitoria Rio de Janeiro      Sao Paulo 
          2641           3779           1724           3486           5305 
      Curitiba  Florianopolis   Porto Alegre   Campo Grande         Cuiaba 
          3012           1623           2913           1809           1476 
       Goiania       Brasilia 
          2423           1811

### Faixa Etária

In [10]:
#Faixas Etárias
pns2013.1 <-  pns2013.1 %>% mutate(faixa_idade=cut(C008,
  breaks = c(18,30, 45, 60, 75,Inf),
  labels = c("18 a 29 anos","30 a 44 anos","45 a 59 anos","60 a 74 anos","75 anos ou mais"), 
  ordered_result = TRUE, right = FALSE))
summary(pns2013.1$faixa_idade) 

18 a 29 anos    30 a 44 anos    45 a 59 anos    60 a 74 anos 75 anos ou mais 
          14321           20242           14462            8290            2887

### Raça

In [11]:
#Raça
pns2013.1 <- pns2013.1 %>% filter(C009!=3|C009!=5|C009!=9)%>% mutate(Raca= ifelse(C009==1, 1, 
                        ifelse(C009==2 , 2, 3)))
pns2013.1$Raca<-factor(pns2013.1$Raca, levels=c(1,2,3),labels=c("Branca", "Preta", "Parda"))
summary(pns2013.1$Raca)

Branca  Preta  Parda 
 24106   5631  30465

### Renda per capita

In [12]:
#Rendimento domiciliar per capita

pns2013.1 <-  pns2013.1 %>% drop_na(VDF003) %>% mutate(rend_per_capita=cut(VDF003,
  breaks = c(-Inf,339, 678, 1356, 2034,Inf),
  labels=c("Ate 1/2 SM","1/2 ate 1 SM","1 ate 2 SM","2 ate 3 SM","Mais de 3 SM"), 
  ordered_result = TRUE, right = TRUE, na.exclude= TRUE))

summary(pns2013.1$rend_per_capita)


Ate 1/2 SM 1/2 ate 1 SM   1 ate 2 SM   2 ate 3 SM Mais de 3 SM 
       14256        17504        15493         5335         7603

### Escolaridade

In [13]:
# Escolaridade
pns2013.1 <- pns2013.1 %>% mutate(gescol = ifelse(VDD004A %in% 1:2, 1, 
                        ifelse(VDD004A%in% 3:4, 2, 
                        ifelse(VDD004A%in% 5:6, 3,4
                        ))))

pns2013.1$gescol<-factor(pns2013.1$gescol, levels=c(1,2,3,4), 
                                  labels=c("Sem instrucao e fundamental incompleto","Fundamental completo e medio incompleto",
                                           "Medio completo e superior incompleto","Superior completo"))
summary(pns2013.1$gescol)

Sem instrucao e fundamental incompleto Fundamental completo e medio incompleto 
                                  24080                                    9212 
   Medio completo e superior incompleto                       Superior completo 
                                  19145                                    7754

## Criando indicadores

### Filtrando base de indicadores

In [14]:
#Selecionando variáveis para cálculo de indicadores no survey_ALTERAR
pns2013Psurvey<- pns2013.1 %>% select("V0024","UPA_PNS","peso_morador_selec", "P010P","P011P","P012P", "P013P",
                                    "C008","V0031", "Sit_Urbano_Rural","Sexo","Unidades_da_Federacao", "GrandesRegioes",
                                     "Capital","faixa_idade", "Raca","rend_per_capita","gescol")
summary(pns2013Psurvey)

     V0024            UPA_PNS        peso_morador_selec  P010P      
 Min.   :1110011   Min.   :1100001   Min.   : 0.004156   Sim:13223  
 1st Qu.:2210013   1st Qu.:2200075   1st Qu.: 0.243935   Nao:46968  
 Median :2951023   Median :2900192   Median : 0.521557              
 Mean   :3035304   Mean   :3007768   Mean   : 1.000020              
 3rd Qu.:4110111   3rd Qu.:4100002   3rd Qu.: 1.147380              
 Max.   :5310220   Max.   :5300180   Max.   :31.179597              
                                                                    
 P011P       P012P       P013P            C008            V0031      
 Sim: 1346   Sim: 8100   Sim: 2361   Min.   : 18.00   Min.   :1.000  
 Nao:58845   Nao:52091   Nao:57830   1st Qu.: 30.00   1st Qu.:1.000  
                                     Median : 41.00   Median :2.000  
                                     Mean   : 43.32   Mean   :2.308  
                                     3rd Qu.: 55.00   3rd Qu.:4.000  
                            

### Exporta tabela filtrada

In [ ]:
#Salvando csv para cálculo de indicadores no survey_ALTERAR
path <- "<coloque aqui o caminho onde deseja salvar a base filtrada>"
write.csv(pns2013Psurvey, file.path(path, "pns2013Psurvey.csv"))

### Cria plano amostral complexo

In [15]:
#survey design
desPNSP=svydesign(id=~UPA_PNS, strat=~V0024, weight=~peso_morador_selec, nest=TRUE, data=pns2013Psurvey)
desPNSP18=subset(desPNSP, C008>=18)
desPNSPC=svydesign(id=~UPA_PNS, strat=~V0024, weight=~peso_morador_selec, nest=TRUE, data=pns2013Psurvey)
desPNSPC18=subset(desPNSPC, C008>=18 & V0031==1)

### Criação da tabela de indicadores
Essa tabela é responsável por unir os indicadores no formato do painel de indicadores

In [29]:
matrizIndicadores = data.frame()

#### Definição de variáveis para iteração dos indicadores

In [30]:
#Cálculo dos indicadores usando o pacote survey - alterar
ListaIndicadores = c(~P010P,~P011P,~P012P,~P013P)
ListaIndicadoresTexto = c("P010P","P011P","P012P","P013P")
ListaDominios = c(~Sexo,~Raca,~rend_per_capita,~faixa_idade,~Sit_Urbano_Rural,~Unidades_da_Federacao,~GrandesRegioes,~Capital,~gescol)
ListaDominiosTexto = c("Sexo","raca","rend_per_capita","fx_idade_18","urb_rur","uf","regiao","capital","gescol")
ListaTotais = c('Brasil','Capital')
Ano <- "2013"

ListaTotais = c('Brasil','Capital')
Ano <- "2013"ListaTotais = c('Brasil','Capital')
Ano <- "2013"#### Preenchendo a tabela de indicadores
Essas iterações rodam por indicador, abrangência e por design

In [31]:
i <- 0
for( indicador in ListaIndicadores){
    i <- i + 1
    j <- 1
    for (dominio in ListaDominios){
               if (ListaDominiosTexto[j]=="capital"){
                   dataframe_indicador<-svyby( indicador , dominio , desPNSPC18 , svymean,vartype=c("ci","cv"))
               }else{
                    dataframe_indicador<-svyby( indicador , dominio , desPNSP18 , svymean,vartype=c("ci","cv"))
                    }
               dataframe_indicador<-data.frame(dataframe_indicador)
               
               colnames(dataframe_indicador) <- c("abr_nome","Sim","Nao","LowerS","LowerN","UpperS","UpperN","cvS","cvN")
               dataframe_indicador$Indicador <- ListaIndicadoresTexto[i]
               dataframe_indicador$abr_tipo <- ListaDominiosTexto[j]
               dataframe_indicador$Ano <- Ano
               dataframe_indicador <- dataframe_indicador %>% select("abr_tipo","abr_nome","Ano","Indicador","Sim","LowerS","UpperS","cvS")
               matrizIndicadores <-rbind(matrizIndicadores,dataframe_indicador)
               j <- j + 1
               
    }
}



#### Criando a tabela pela abrangência total

In [33]:
matriz_totais <- data.frame()

#### Preenchendo a tabela com as abrangencia Brasil e total das capitais

In [34]:
i=0
for(indicador in ListaIndicadores){
    i <- i+1
    for(total in ListaTotais){
        dataframe_indicador <- data.frame()
        dataframe_indicador_S <- data.frame()
        dataframe_indicador_N <- data.frame()
        if(total == 'Capital'){
            dataframe_indicador <- svymean(indicador,desPNSPC18)
        }else{
            dataframe_indicador <- svymean(indicador,desPNSP18)
        }
        intervalo_confianca <- confint(dataframe_indicador)
        coeficiente_variacao <- cv(dataframe_indicador)
        dataframe_indicador <- cbind(data.frame(dataframe_indicador),data.frame(intervalo_confianca))
        dataframe_indicador <- cbind(data.frame(dataframe_indicador),data.frame(coeficiente_variacao))

        dataframe_indicador <- dataframe_indicador %>% 
                               select('mean','X2.5..','X97.5..',coeficiente_variacao) 
        
        dataframe_indicador <- dataframe_indicador %>% 
                                 slice(1)
        colnames(dataframe_indicador) <- c('Sim','LowerS','UpperS','cvS')
        dataframe_indicador <- dataframe_indicador %>% 
                               select('Sim','LowerS','UpperS','cvS')
        dataframe_indicador$Indicador <- ListaIndicadoresTexto[i]
        dataframe_indicador$abr_tipo <- "total"
        dataframe_indicador$abr_nome <- total
        dataframe_indicador$Ano <- Ano 
        dataframe_indicador <- dataframe_indicador %>% 
                             select("abr_tipo","abr_nome","Ano","Indicador",'Sim','LowerS','UpperS','cvS')
       
        matriz_totais <-rbind(matriz_totais,dataframe_indicador)
        
    }
}

#### Unindo tabela de indicadores e de totais

In [35]:
matrizIndicadores<-rbind(matrizIndicadores,matriz_totais)

#### Exportando tabela de indicadores

In [22]:
write.table(matrizIndicadores,file="<coloque aqui o caminho para exportação da matriz de indicadores>",sep = ";",dec = ",",row.names = FALSE)